In [2]:
import numpy as np
import matplotlib.pyplot as plt
import csv
import numpy.linalg as LA
import random
import pandas as pd
from numpy import inf
import torch
from torch import nn
import matplotlib
matplotlib.use('Agg')
import matplotlib.pyplot as plt
import torch.optim as optim
import json
import itertools
import math
import pyprind
from random import sample

In [3]:
#f = open('data_irl_model/Feb23_data_exploratory_policy.json')
f = open('../data_irl_model/Feb22_dataSVO.json')
data_irl = json.load(f)

In [4]:
data_keys=list(data_irl.keys())
data_keys.sort()

keys_for_training=[]
keys_for_testing=[]

index=0
for vehicle in data_keys:
    if index%10==0:
        keys_for_testing.append(vehicle)
        index+=1
    else:
        keys_for_training.append(vehicle)
        index+=1

In [4]:
len(keys_for_training)

5400

In [ ]:
data_irl[str(keys_for_testing[10])]

In [5]:
key=keys_for_training[967]
key=str(key)                
############# Create the data for the training locally- we are restricting the number of timesteps to num_timesteps######
negative_vals=[]
for i in [0,1]:
    negative_vals.append(list(filter(lambda x: x < 1, data_irl[key][i])))
num_timesteps=min(20,len(negative_vals[0]),len(negative_vals[1]))

print("0: ", negative_vals[0])
print("1: ", negative_vals[1])

print("num_timesteps: ", num_timesteps)

0:  [-50.0, -48.1, -46.4, -44.75796913937893, -43.040772632427355, -41.271099841265446, -39.4745449925036, -37.67293664052113, -35.88498649497113, -34.127188049008055, -32.415130406928334, -30.764126999474023, -29.19012274020666, -27.71120188485676, -26.348038955235424, -25.125573218590144, -24.074698426038893, -23.218097074828766, -22.561495723618638, -22.10489437240851, -21.848293021198383, -21.76999234559332, -21.76999234559332, -21.76999234559332, -21.76999234559332, -21.76999234559332, -21.76999234559332, -21.76999234559332, -21.76999234559332, -21.76999234559332, -21.76999234559332, -21.76999234559332, -21.76999234559332, -21.76999234559332, -21.76999234559332, -21.76999234559332, -21.73049042434515, -21.59148658184881, -21.332482739352468, -20.95347889685613, -20.45447505435979, -19.83547121186345, -19.09646736936711, -18.237463526870773, -17.258459684374436, -16.1594558418781, -14.940451999381757, -13.601448156885418, -12.142444314389081, -10.56344047189274, -8.864436629396401,

In [ ]:
index_before_zero=data_irl[key][1].index(negative_vals[1][len(negative_vals[1])-1])
print("index_before_zero: ", index_before_zero)
num_timesteps=20
indices_to_train=[]
if index_before_zero-num_timesteps>=0:
    indices_to_train=range(index_before_zero-num_timesteps,index_before_zero+2)
else:
    indices_to_train=range(0,index_before_zero+2)

for ind in indices_to_train:
    print(data_irl[key][0][ind])
for ind in indices_to_train:
    print(data_irl[key][1][ind])

In [5]:
#########################################################################
################################ AIS_gen ################################

################################ Model 1 ################################ 

class GenerateAis1(nn.Module):

    #def __init__(self,n_input,n_state,n_psi2_in=64,n_psi2_out=128):
    def __init__(self,n_input,n_state,n_psi2_in=8,n_psi2_out=16):
        super(GenerateAis1,self).__init__()
        self.PSI_layer1=nn.Linear(n_input,n_psi2_in)     # Use RELU after
        self.PSI_layer2=nn.Linear(n_psi2_in,n_psi2_out)      # Use RELU after
        self.PSI_layer3=nn.GRUCell(n_psi2_out,n_state)       # This is the Gated layer

    def forward(self,x,h):
        #x=torch.transpose(x,0,1)
        #h=torch.transpose(h,0,1)
        x=torch.relu(self.PSI_layer1(x))
        x=torch.relu(self.PSI_layer2(x))
        h=self.PSI_layer3(x,h)
        return h     


In [6]:
#########################################################################
################################ AIS_pred ###############################

################################ Model 1 ################################ 

class PredictAis1(nn.Module):
    
    #def __init__(self,n_output,n_state,n_phi2_in=16,n_phi2_out=8):
    def __init__(self,n_output,n_state,n_phi2_in=2,n_phi2_out=4):
        super(PredictAis1,self).__init__()
        self.PHI_layer1=nn.Linear(n_state,n_phi2_in)  # Use RELU after
        self.PHI_layer2=nn.Linear(n_phi2_in,n_phi2_out)     # Use RELU after
        self.PHI_layer3=nn.Linear(n_phi2_out,n_output)         # mean vector of a unit-variance multivariate Gaussian distribution, samples from which are used to predict the next observation

    def forward(self,x):
        x=torch.relu(self.PHI_layer1(x))
        x=torch.relu(self.PHI_layer2(x))
        output=self.PHI_layer3(x)
        return output


In [7]:
negative_vals=[]
for i in [0,1]:
    negative_vals.append(list(filter(lambda x: x < 1, data_irl[str(keys_for_testing[0])][i])))
print(negative_vals)

[[-50.0, -48.1, -46.4, -44.761122658207675, -43.05127992142175, -41.28274312577878, -39.46536936838444, -37.60696288521823, -35.71356531742613, -33.78968838023041, -31.838501427503736, -29.861986078108643, -27.861070285758846, -25.835754674634355, -23.785244071125202, -21.708096136013104, -19.60239595060883, -17.4659597386202, -15.29656284320157, -13.092178062307937, -10.851202938627893, -8.573166165623306, -6.259465148147179, -3.913311880225578, -1.5399957277141993, 0.8524037569850123], [-56.30088862147648, -54.726865665496135, -53.206261143616395, -51.740175800649745, -50.32985055901144, -48.97686996364336, -47.68307154610725, -46.450560206681246, -45.281725232740015, -44.17925946401058, -43.1461798219091, -42.18584795159752, -41.30198901475314, -40.49870563862401, -39.7804825945506, -39.15217590591451, -38.61897783980735, -38.186346917018525, -37.85989037368617, -37.64518666049085, -37.54753932832985, -37.528616713070534, -37.528616713070534, -37.528616713070534, -37.528616713070534

In [12]:
class NN_structure(object):
    def __init__(self,n_epochs,min_timesteps,n_rollout,n_test,n_input,n_output,n_state_enc,learning_rate,ais_gen_model,ais_pred_model,device):
        self.n_epochs=n_epochs
        self.min_timesteps=min_timesteps
        self.rollout=n_rollout
        self.n_test=n_test
        self.n_input=n_input
        self.n_output=n_output
        self.n_state_enc=n_state_enc    # Hidden state size in RNN
        self.learning_rate=learning_rate                
        self.device=device
        self.ais_gen_model=ais_gen_model
        self.ais_pred_model=ais_pred_model

        self.n_psi2_in=8
        self.n_psi2_out=16
        self.n_phi2_in=2
        self.n_phi2_out=4
        self.n_psi1_out=8
        
        if ais_gen_model==1:
            self.gen_model=GenerateAis1(self.n_input,self.n_state_enc).to(self.device)      
        
        #if ais_gen_model==2: 
            #self.gen_model=GenerateAis2(self.n_input,self.n_state_enc,self.n_psi1_out).to(self.device)        
            #self.gen_model=GenerateAis2_LSTM(self.n_input,self.n_state_enc,self.n_psi1_out).to(self.device)
            #self.gen_model=GenerateAis_LSTMShallow(self.n_input,self.n_state_enc).to(self.device)  

        if ais_pred_model==1:
            self.pred_model=PredictAis1(self.n_output,self.n_state_enc).to(self.device)
        
        #if ais_pred_model==2:
            #self.pred_model=PredictAis2(self.n_output,self.n_state_enc+1,self.n_state_dec).to(self.device)
            #self.pred_model=PredictAis2_LSTM(self.n_output,self.n_state_enc+1,self.n_state_dec).to(self.device)
            #self.pred_model=PredictAis_LSTMShallow(self.n_state_enc+1,self.n_state_dec).to(self.device)

    def save_model_weights(self,text="(:*_*:)"):
        #name_gen_path="trained_models/IRL_based_models/IRL_SVOpolicy_ais_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+text+".pth"
        #torch.save(self.gen_model.state_dict(),name_gen_path)
        
        name_gen_path="_"
        name_pred_path="_"
        if self.ais_pred_model==1:
            name_pred_path="../trained_models/IRL_based_models/IRL_SVOpolicy_ais_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+text+".pth"
            name_gen_path="../trained_models/IRL_based_models/IRL_SVOpolicy_ais_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+text+".pth"

        if self.ais_pred_model==2:
            name_pred_path="../trained_models/IRL_based_models/IRL_SVOpolicy_multi_rnn_ais_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+"_"+str(self.n_state_dec)+text+".pth"
            name_gen_path="../trained_models/IRL_based_models/IRL_SVOpolicy_multi_rnn_ais_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+"_"+str(self.n_state_dec)+text+".pth"

        torch.save(self.gen_model.state_dict(),name_gen_path)
        torch.save(self.pred_model.state_dict(),name_pred_path)

        return "saved"
    
    def load_model_weights(self,text="_"):
        #name_gen_path="trained_models/IRL_based_models/IRL_SVOpolicy_ais_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+text+".pth"
        #torch.save(self.gen_model.state_dict(),name_gen_path)
        #self.gen_model.load_state_dict(torch.load(name_gen_path))
        #self.gen_model.eval()

        name_gen_path="_"
        name_pred_path="_"
        
        if self.ais_pred_model==1:
            name_pred_path="../trained_models/IRL_based_models/IRL_SVOpolicy_ais_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+text+".pth"
            name_gen_path="../trained_models/IRL_based_models/IRL_SVOpolicy_ais_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+text+".pth"

        if self.ais_pred_model==2:
            name_pred_path="../trained_models/IRL_based_models/IRL_SVOpolicy_multi_rnn_ais_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+"_"+str(self.n_state_dec)+text+".pth"
            name_gen_path="../trained_models/IRL_based_models/IRL_SVOpolicy_multi_rnn_ais_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+"_"+str(self.n_state_dec)+text+".pth"
        
        #torch.save(self.pred_model.state_dict(),name_pred_path)
        self.gen_model.load_state_dict(torch.load(name_gen_path))
        self.gen_model.eval()

        self.pred_model.load_state_dict(torch.load(name_pred_path))
        self.pred_model.eval()

        return "loaded"
    

    def train(self):
        train_bar=pyprind.ProgBar(self.n_epochs)
        self.optimizer = torch.optim.Adam(list(self.gen_model.parameters()) + list(self.pred_model.parameters()), lr=self.learning_rate, amsgrad=True)

        time_step_loss=0
        for epoch in range(self.n_epochs):

            train_bar.update()
            keys_training=sample(keys_for_training,len(keys_for_training)) #shuffle the keys
            #train_bar=pyprind.ProgBar(len(keys_for_training))
            epoch_loss=0
            for key in keys_training:
                #for key in keys_for_testing[0]:
                #train_bar.update()
                key=str(key) 
                               
                ############# Create the data for the training locally- we are restricting the number of timesteps to num_timesteps ######
                negative_vals=[]
                for i in [0,1]:
                    negative_vals.append(list(filter(lambda x: x < 1, data_irl[key][i])))
                num_timesteps=min(self.min_timesteps,len(negative_vals[0]),len(negative_vals[1]))
                index_before_zero=data_irl[key][1].index(negative_vals[1][len(negative_vals[1])-1])
                #print("index_before_zero: ", index_before_zero)
                num_timesteps=20
                indices_to_train=[]
                if index_before_zero-num_timesteps>=0:
                    indices_to_train=range(index_before_zero-num_timesteps,index_before_zero+1)
                else:
                    indices_to_train=range(0,index_before_zero+2)
                #print("ndices_to_train: ", indices_to_train)
                #######################################

                #### IMPORTANT Cropping the indices as per availability of data - 
                # What if index_before_zero == length of the list and we are looking 
                # to predict data that is in existent
                indices_to_train_cropped=[]
                if index_before_zero in [len(data_irl[key][1])-1,len(data_irl[key][1])-2,len(data_irl[key][1])-3]:
                    indices_to_train_cropped=indices_to_train[0:-1*self.rollout]
                else:
                    indices_to_train_cropped=indices_to_train

                # Ais initialization
                ais_rollout_enc=0.5*torch.ones(self.n_state_enc,dtype=torch.float).to(self.device)
                state_rollout_enc=0.5*torch.ones(self.n_state_enc,dtype=torch.float).to(self.device) # Only if we use a LSTM
                action_list=[0,0] ## initialize the action list differently - but we can try giving it the actual values to iterate                

                time_step_loss=0

                # Initialize the origin offset only for position
                origin_offset_CAV=data_irl[key][0][indices_to_train[0]]
                origin_offset_HDV=data_irl[key][1][indices_to_train[0]]


                for time_step in indices_to_train_cropped:

                    observation_list=[]
                    for i in range(len(data_irl[key])-2): # exclude the last two columns (actions/inputs)
                        temp=data_irl[key][i][time_step]
                        if i==0:
                            temp=temp-origin_offset_CAV
                        elif i==1:
                            temp=temp-origin_offset_HDV
                        if temp!= None:
                            observation_list.append(temp)
                    input_list=[]
                    input_list.extend(observation_list)
                    input_list.extend(action_list)
                    input_tensor=torch.tensor(input_list,dtype=torch.float).to(self.device)                    

                    # Update action list for the next time step 
                    for i in [4,5]:
                        temp=data_irl[key][i][time_step]
                        if temp!= None:
                            action_list[i-4]=temp
                        else:
                            action_list[i-4]=0

                    reference_list=[]
                    for k in range(self.rollout):
                        for i in [1,3,5]:#range(len(data_irl[key])):
                            if i==1:# min is self.rollout
                                #rint("key",key)
                                #print("i",i)
                                #print("time_step+k+1",time_step+k+1)
                                reference_list.append(data_irl[key][i][time_step+k+1]-origin_offset_HDV)
                            
                            elif i==3:
                                reference_list.append(data_irl[key][i][time_step+k+1])

                            elif i>=4 and data_irl[key][i][time_step+k]!=None: # Previous action is observed at time_step+k+1
                                reference_list.append(data_irl[key][i][time_step+k])
                            
                            else:
                                reference_list.append(0) # Zero padding for the input action

                    '''
                    # This is to be as 3* as long as the number of rollouts - 3 for each rollout
                    internal_rollout=min(self.rollout,len(data_irl[key][0])-time_step-2)
                    

                    reference_list=[]

                    if internal_rollout==self.rollout:
                        for k in range(self.rollout):
                            for i in [1,3,5]:#range(len(data_irl[key])):
                                if i==1:# min is self.rollout
                                    reference_list.append(data_irl[key][i][time_step+k+1]-origin_offset_HDV)
                                
                                elif i==3:
                                    reference_list.append(data_irl[key][i][time_step+k+1])

                                elif i>=4 and data_irl[key][i][time_step+k]!=None: # Previous action is observed at time_step+k+1
                                    reference_list.append(data_irl[key][i][time_step+k])
                                
                                else:
                                    reference_list.append(0) # Zero padding for the input action
                            
                    else:
                        for k in range(internal_rollout):
                            for i in [1,3,5]:#range(len(data_irl[key])):
                                if i==1:# min is not self.rollout
                                    reference_list.append(data_irl[key][i][time_step+k+1]-origin_offset_HDV)
                                
                                elif i==3:
                                    reference_list.append(data_irl[key][i][time_step+k+1])

                                elif i>=4 and data_irl[key][i][time_step+k]!=None: # Previous action is observed at time_step+k+1
                                    reference_list.append(data_irl[key][i][time_step+k])
                                
                                else:
                                    reference_list.append(0) # Zero padding for the input action
                                    
                        for k in range(internal_rollout,self.rollout):
                            for i in [1,3,5]:
                                reference_list.append(0)
                    '''


                    reference_tensor=torch.tensor(reference_list,dtype=torch.float).to(self.device)

                    ais_rollout_enc=self.gen_model(input_tensor,ais_rollout_enc)
                    decoder_prediction=self.pred_model(ais_rollout_enc)

                    ## Mulitvariate normal distribution loss
                    #time_step_loss+=torch.distributions.MultivariateNormal(decoder_prediction,torch.eye(self.n_output).to(self.device)).log_prob(reference_tensor)
                    ## MSE loss
                    time_step_loss+=torch.nn.functional.mse_loss(decoder_prediction,reference_tensor)                    
                    #print("time_step_loss: ",time_step_loss)
                    print("reference_tensor: ",reference_tensor)
                    print("decoder_prediction: ",decoder_prediction,"\n")
                    
                    
               
                epoch_loss+=time_step_loss
                self.optimizer.zero_grad()
                time_step_loss.backward()
                self.optimizer.step()
                
                ## Printing the gradients
                '''
                print("Printing the gradients-encoder")
                print(self.gen_model.PSI_layer3.weight_ih.grad)
                print(self.gen_model.PSI_layer3.weight_hh.grad)
                print(self.gen_model.PSI_layer3.bias_ih.grad)
                print(self.gen_model.PSI_layer3.bias_hh.grad)

                print("Printing the gradients-decoder")                
                print(self.pred_model.PHI_layer1.weight.grad)
                print(self.pred_model.PHI_layer2.weight.grad)
                print(self.pred_model.PHI_layer3.weight.grad)           
                '''
                
            print("epoch_loss is ",epoch_loss,"\n")                
            print("saving model weights for epoch ",epoch)
            status=self.save_model_weights("encoder_rnn_decoder_simple_nn_n_rollout_3")




In [13]:
####### Parameters #######
n_epochs=1
min_timesteps=15
n_rollout=1
n_test=1
n_input=6
n_output=n_rollout*3 # 3 for each of the next n_rollout time steps
n_state_enc=4
learning_rate=0.05
gen_model=1
pred_model=1
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

In [14]:
####### Initialise the neural network #######

network=NN_structure(n_epochs,min_timesteps,n_rollout,n_test,n_input,n_output,n_state_enc,learning_rate,gen_model,pred_model,device)
print("Training has started")
network.train()


Training has started


0% [#] 100% | ETA: 00:00:00

reference_tensor:  tensor([1.7559, 8.8871, 1.0765], device='cuda:0')
decoder_prediction:  tensor([0.3090, 0.4821, 0.6095], device='cuda:0', grad_fn=<AddBackward0>) 

reference_tensor:  tensor([3.5527, 9.0815, 0.9719], device='cuda:0')
decoder_prediction:  tensor([0.2880, 0.4997, 0.6085], device='cuda:0', grad_fn=<AddBackward0>) 

reference_tensor:  tensor([5.3866, 9.2574, 0.8796], device='cuda:0')
decoder_prediction:  tensor([0.2762, 0.5096, 0.6080], device='cuda:0', grad_fn=<AddBackward0>) 

reference_tensor:  tensor([7.2541, 9.4172, 0.7992], device='cuda:0')
decoder_prediction:  tensor([0.2731, 0.5121, 0.6078], device='cuda:0', grad_fn=<AddBackward0>) 

reference_tensor:  tensor([9.1521, 9.5632, 0.7301], device='cuda:0')
decoder_prediction:  tensor([0.2731, 0.5121, 0.6078], device='cuda:0', grad_fn=<AddBackward0>) 

reference_tensor:  tensor([11.0782,  9.6976,  0.6718], device='cuda:0')
decoder_prediction:  tensor([0.2731, 0.5121, 0.6078], device='cuda:0', grad_fn=<AddBackward0>) 

r


Total time elapsed: 00:00:00


tensor([1.8531, 9.5653, 3.0000], device='cuda:0')
decoder_prediction:  tensor([0.3848, 0.6319, 0.5606], device='cuda:0', grad_fn=<AddBackward0>) 

reference_tensor:  tensor([ 3.8261, 10.1653,  3.0000], device='cuda:0')
decoder_prediction:  tensor([0.3848, 0.6319, 0.5606], device='cuda:0', grad_fn=<AddBackward0>) 

reference_tensor:  tensor([ 5.9192, 10.7653,  3.0000], device='cuda:0')
decoder_prediction:  tensor([0.3848, 0.6319, 0.5606], device='cuda:0', grad_fn=<AddBackward0>) 

reference_tensor:  tensor([ 8.1292, 11.3349,  2.8482], device='cuda:0')
decoder_prediction:  tensor([0.3848, 0.6319, 0.5606], device='cuda:0', grad_fn=<AddBackward0>) 

reference_tensor:  tensor([10.4054, 11.4277,  0.4640], device='cuda:0')
decoder_prediction:  tensor([0.3848, 0.6319, 0.5606], device='cuda:0', grad_fn=<AddBackward0>) 

reference_tensor:  tensor([12.6914, 11.4316,  0.0196], device='cuda:0')
decoder_prediction:  tensor([0.3848, 0.6319, 0.5606], device='cuda:0', grad_fn=<AddBackward0>) 

referenc

KeyboardInterrupt: 

In [37]:
#key= 2825
#i= 1
#time_step+k+1 =201

data_irl[str(2825)][1][200]

key=str(2825)

############# Create the data for the training locally- we are restricting the number of timesteps to num_timesteps ######
negative_vals=[]
for i in [0,1]:
    negative_vals.append(list(filter(lambda x: x < 1, data_irl[key][i])))
num_timesteps=min(15,len(negative_vals[0]),len(negative_vals[1]))
index_before_zero=data_irl[key][1].index(negative_vals[1][len(negative_vals[1])-1])
#print("index_before_zero: ", index_before_zero)
num_timesteps=20
indices_to_train=[]
if index_before_zero-num_timesteps>=0:
    indices_to_train=range(index_before_zero-num_timesteps,index_before_zero+1)
    print("ndices_to_train: if ", indices_to_train)
else:
    indices_to_train=range(0,index_before_zero+2)
    print("ndices_to_train: else ", indices_to_train)
#######################################
print("values and index near zero",index_before_zero,len(data_irl[key][1]))
#print(data_irl[key][1][index_before_zero-1])
#print(data_irl[key][1][index_before_zero])
#print(data_irl[key][1][index_before_zero+1])

#### IMPORTANT Cropping the indices as per availability of data - 
# What if index_before_zero == length of the list and we are looking 
# to predict data that is in existent
indices_to_train_cropped=[]
if index_before_zero in [len(data_irl[key][1])-1,len(data_irl[key][1])-2,len(data_irl[key][1])-3]:
    indices_to_train_cropped=indices_to_train[0:-3]
else:
    indices_to_train_cropped=indices_to_train

for time_step in indices_to_train_cropped:
    reference_list=[]
    for k in range(1):
        i=1# min is self.rollout
        print("key",key)
        print("i",i)
        print("time_step+k+1",time_step+k+1)
        reference_list.append(data_irl[key][i][time_step+k+1]-50)
        print(reference_list)

ndices_to_train: if  range(180, 201)
values and index near zero 200 201
key 2825
i 1
time_step+k+1 181
[-66.29892940081835]
key 2825
i 1
time_step+k+1 182
[-65.9601027255325]
key 2825
i 1
time_step+k+1 183
[-65.61655776985745]
key 2825
i 1
time_step+k+1 184
[-65.26828988218404]
key 2825
i 1
time_step+k+1 185
[-64.91529466045202]
key 2825
i 1
time_step+k+1 186
[-64.55756794643409]
key 2825
i 1
time_step+k+1 187
[-64.19510582018441]
key 2825
i 1
time_step+k+1 188
[-63.82790459464648]
key 2825
i 1
time_step+k+1 189
[-63.45596081041402]
key 2825
i 1
time_step+k+1 190
[-63.07927123063986]
key 2825
i 1
time_step+k+1 191
[-62.69783283608741]
key 2825
i 1
time_step+k+1 192
[-62.31164282031967]
key 2825
i 1
time_step+k+1 193
[-61.92069858502114]
key 2825
i 1
time_step+k+1 194
[-61.52499773544789]
key 2825
i 1
time_step+k+1 195
[-61.12453807600144]
key 2825
i 1
time_step+k+1 196
[-60.719317605922285]
key 2825
i 1
time_step+k+1 197
[-60.30933451509884]
key 2825
i 1
time_step+k+1 198
[-59.89458717

In [229]:
# Test the network

####### Load the neural network weights from saved models #######

loaded_network=NN_structure(n_epochs,min_timesteps,n_rollout,n_test,n_input,n_output,n_state_enc,learning_rate,gen_model,pred_model,device)
loaded_network.load_model_weights("reduced_timesteps15_Rollout_1_added_time_step_to_decoder_input_minusall_magerr100")


test_keys=[keys_for_testing[15]]
test_results=loaded_network.test(test_keys)

0% [#] 100% | ETA: 00:00:00
Total time elapsed: 00:00:00




Before rollout, the input is  tensor([-50.0000, -50.1345,  10.0000,   5.3078,   0.0000,   0.0000],
       device='cuda:0')
for rollout 0 ais  tensor([0.5000, 0.5000], device='cuda:0')
for rollout 0 rollout_reference is  tensor([-4.9073e+01,  5.3081e+00,  1.8404e-03], device='cuda:0')
for rollout 0 decoder_input  is  tensor([1., 1., 0.], device='cuda:0', grad_fn=<CatBackward0>) 0
for rollout 0 rollout_prediction is  tensor([-0.0000, -0.0000, -1.3220], device='cuda:0', grad_fn=<NegBackward0>)


Before rollout, the input is  tensor([-4.8100e+01, -4.9073e+01,  9.0000e+00,  5.3081e+00, -5.0000e+00,
         1.8404e-03], device='cuda:0')
for rollout 0 ais  tensor([1., 1.], device='cuda:0', grad_fn=<SqueezeBackward1>)
for rollout 0 rollout_reference is  tensor([-4.8011e+01,  5.3085e+00,  1.6556e-03], device='cuda:0')
for rollout 0 decoder_input  is  tensor([1., 1., 1.], device='cuda:0', grad_fn=<CatBackward0>) 1
for rollout 0 rollout_prediction is  tensor([-0.0000, -0.0000, -1.3517], device

In [214]:
test_results.test_run_comparision

[[[-49.07296, 5.3081274, 0.0018403638, -18.169144, 5.5449357, -1.6968961]],
 [[-48.011303, 5.3084583, 0.0016555589, -18.171122, 5.5455713, -1.6971188]],
 [[-46.94958, 5.3087554, 0.0014832187, -18.171967, 5.545838, -1.6972182]],
 [[-45.887806, 5.3090115, 0.0012823439, -18.172344, 5.545954, -1.697264]],
 [[-44.82598, 5.3092246, 0.0010645859, -18.17252, 5.5460067, -1.6972859]],
 [[-43.76412, 5.3093905, 0.00082904915, -18.172604, 5.5460324, -1.6972971]],
 [[-42.70223, 5.3095055, 0.00057430426, -18.172646, 5.5460453, -1.6973026]],
 [[-41.640324, 5.309565, 0.00029867006, -18.172668, 5.546051, -1.6973054]],
 [[-40.57841, 5.309565, 1.7601678e-07, -18.17268, 5.5460544, -1.6973069]],
 [[-39.516502, 5.3095, -0.0003234884, -18.172684, 5.546056, -1.6973078]],
 [[-38.454617, 5.3093653, -0.00067481643, -18.172688, 5.5460567, -1.6973081]],
 [[-37.392765, 5.309154, -0.0010562867, -18.17269, 5.5460577, -1.6973085]],
 [[-36.330963, 5.30886, -0.0014708722, -18.172688, 5.546057, -1.6973083]],
 [[-35.26923,

In [ ]:
## Test function ##
def test(self,test_keys):
    test_bar=pyprind.ProgBar(len(test_keys))
    self.comparision_list=[]
    #self.load_model_weights("Rollout_10")
    #print("loaded model weights")
        
    self.test_run_comparision=[]
    for test_run in range(len(test_keys)):
        test_bar.update()
        #key_test=str(test_keys[test_run])
        #key_test=str(keys_for_training[test_run])
        key_test=keys_for_training[0]
        
        ############# locally restrict the data for the training - we are restricting the number of timesteps to num_timesteps######
        negative_vals=[]
        for i in [0,1]:
            negative_vals.append(list(filter(lambda x: x < 1, data_irl[key_test][i])))

        num_timesteps=min(self.min_timesteps,len(negative_vals[0]),len(negative_vals[1]))
        
        # Ais initialization
        time_step_loss=0
        ais_rollout_enc=0.5*torch.ones(self.n_state_enc,dtype=torch.float).to(self.device)
        action_list=[0,0]             

        time_step_comparision=[]
        for time_step in range(num_timesteps):                    
            observation_list=[]
            for i in range(len(data_irl[key_test])-2): # exclude the last two columns (actions/inputs)
                temp=data_irl[key_test][i][time_step]
                if temp!= None:
                    observation_list.append(temp)
                
            input_list=[]
            input_list.extend(observation_list)
            input_list.extend(action_list)
            input_tensor=torch.tensor(input_list,dtype=torch.float).to(self.device)
            print("\n")
            print("Before rollout, the input is ",input_tensor)
            # Update action list for the next time step and for the reference
            for i in [4,5]:
                temp=data_irl[key_test][i][time_step]
                if temp!= None:
                    action_list[i-4]=temp
                else:
                    action_list[i-4]=0

            reference_list=[]
            observation_list_ref=[]
            for i in [1,3]:#range(len(data_irl[key_test])-2): # exclude the last two columns (actions/inputs)
                temp=data_irl[key_test][i][time_step+1]
                if temp!= None:
                    observation_list_ref.append(temp)                      
            reference_list.extend(observation_list_ref)
            reference_list.extend([action_list[1]])

            reference_tensor=1*torch.tensor(reference_list,dtype=torch.float).to(self.device)

            ais_rollout_dec=0.5*torch.ones(self.n_state_dec,dtype=torch.float).to(self.device) # Just initialize it to 0.5


            rollout_reference=0.5*torch.ones(self.n_output,dtype=torch.float).to(self.device)

            rollout_prediction=0.5*torch.ones(self.n_output,dtype=torch.float).to(self.device)

            #internal_rollout_horizon=min(self.rollout,len(data_irl[key_test][0])-time_step-2)
            internal_rollout_horizon=1
            rollout_loss=0

            rollout_comparison=[]
            for k in range(internal_rollout_horizon):
                temp_comparision=[]
                
                #print("\n")
                if k==0:
                    rollout_input=input_tensor
                    rollout_reference=reference_tensor
                    #ais_rollout_enc=ais
                    print("for rollout",k,"ais ",ais_rollout_enc)

                    ais_rollout_enc=self.gen_model(rollout_input,ais_rollout_enc)
                    #ais=ais_rollout_enc
                    
                    #decoder_input=list(ais_rollout_enc.detach().cpu().numpy())
                    #decoder_input.extend([time_step+k])
                    #decoder_input_tensor=torch.tensor(decoder_input,dtype=torch.float).to(self.device)
                    
                    time_step_tensor=torch.tensor([time_step+k],dtype=torch.float).to(self.device)
                    decoder_input_tensor=torch.cat((ais_rollout_enc,time_step_tensor),0)
                    rollout_prediction,ais_rollout_dec=self.pred_model(decoder_input_tensor,ais_rollout_dec)
                    
                    print("for rollout",k,"rollout_reference is ",rollout_reference)
                    print("for rollout",k,"decoder_input  is ",decoder_input_tensor,time_step+k)
                    print("for rollout",k,"rollout_prediction is ",rollout_prediction)
                    
                    rollout_loss+=-torch.distributions.MultivariateNormal(rollout_prediction,torch.eye(rollout_prediction.shape[0]).to(self.device)).log_prob(rollout_reference)

                    temp_comparision.extend(rollout_reference.detach().cpu().numpy())
                    temp_comparision.extend(rollout_prediction.detach().cpu().numpy())

                else:
                    rollout_reference_list=[]                           
                    for i in [1,3,5]:#range(len(data_irl[key_test])):
                        if i<4:
                            rollout_reference_list.append(data_irl[key_test][i][time_step+k+1])
                        elif i>=4 and data_irl[key_test][i][time_step+k]!=None: # Previous action is observed at time_step+k+1
                            rollout_reference_list.append(data_irl[key_test][i][time_step+k])
                        else:
                            rollout_reference_list.append(0) # Zero padding for the input action

                    rollout_reference=1*torch.tensor(rollout_reference_list,dtype=torch.float).to(self.device)

                    
                    #decoder_input=list(ais_rollout_enc.detach().cpu().numpy())
                    #decoder_input.extend([time_step+k])
                    #decoder_input_tensor=torch.tensor(decoder_input,dtype=torch.float).to(self.device)

                    time_step_tensor=torch.tensor([time_step+k],dtype=torch.float).to(self.device)
                    decoder_input_tensor=torch.cat((ais_rollout_enc,time_step_tensor),0)
                    rollout_prediction,ais_rollout_dec=self.pred_model(decoder_input_tensor,ais_rollout_dec)                                                
                    
                    print("for rollout",k,"rollout_reference is ",rollout_reference)
                    print("for rollout",k,"decoder_input  is ",decoder_input_tensor,time_step+k)
                    print("for rollout",k,"rollout_prediction is ",rollout_prediction)

                    temp_comparision.extend(rollout_reference.detach().cpu().numpy())
                    temp_comparision.extend(rollout_prediction.detach().cpu().numpy())
                    rollout_loss+=-torch.distributions.MultivariateNormal(rollout_prediction,torch.eye(rollout_prediction.shape[0]).to(self.device)).log_prob(rollout_reference)
                rollout_comparison.append(temp_comparision)
            time_step_comparision.append(rollout_comparison)    
        self.test_run_comparision.extend(time_step_comparision)

    return self

In [86]:
#print(len(test_results.test_run_comparision[0][1]))

#test_results.test_run_comparision[19][:]


# Plot the results only for the HDV
pos_t=[]
vel_t=[]
acc_t=[]
pos_tref=[]
vel_tref=[]
acc_tref=[]
pos_t_hdv=[]
vel_t_hdv=[]
acc_t_hdv=[]
pos_tref_hdv=[]
vel_tref_hdv=[]
acc_tref_hdv=[]

# set which timestep to plot
time_step=10

for index in range(len(test_results.test_run_comparision[time_step])):
    '''
    pos_tref.append(test_results.test_run_comparision[time_step][index][0])
    vel_tref.append(test_results.test_run_comparision[time_step][index][2])
    acc_tref.append(test_results.test_run_comparision[time_step][index][4])
    pos_t.append(test_results.test_run_comparision[time_step][index][6])
    vel_t.append(test_results.test_run_comparision[time_step][index][8])
    acc_t.append(test_results.test_run_comparision[time_step][index][10])
    
    #pos_t_hdv.append(test_results.test_run_comparision[time_step][index][1])
    #vel_t_hdv.append(test_results.test_run_comparision[time_step][index][3])
    #acc_t_hdv.append(test_results.test_run_comparision[time_step][index][5])
    #pos_tref_hdv.append(test_results.test_run_comparision[time_step][index][7])
    #vel_tref_hdv.append(test_results.test_run_comparision[time_step][index][9])
    #acc_tref_hdv.append(test_results.test_run_comparision[time_step][index][11])

    
    pos_tref_hdv.append(test_results.test_run_comparision[time_step][index][1])
    vel_tref_hdv.append(test_results.test_run_comparision[time_step][index][3])
    acc_tref_hdv.append(test_results.test_run_comparision[time_step][index][5])
    pos_t_hdv.append(test_results.test_run_comparision[time_step][index][7])
    vel_t_hdv.append(test_results.test_run_comparision[time_step][index][9])
    acc_t_hdv.append(test_results.test_run_comparision[time_step][index][11])
    '''

    pos_tref_hdv.append(test_results.test_run_comparision[time_step][index][0])
    vel_tref_hdv.append(test_results.test_run_comparision[time_step][index][1])
    acc_tref_hdv.append(test_results.test_run_comparision[time_step][index][2])
    pos_t_hdv.append(test_results.test_run_comparision[time_step][index][3])
    vel_t_hdv.append(test_results.test_run_comparision[time_step][index][4])
    acc_t_hdv.append(test_results.test_run_comparision[time_step][index][5])


IndexError: list index out of range

In [ ]:
plot_data=data_irl[str(keys_for_testing[10])]    

pos_t_hdv=[]
vel_t_hdv=[]
acc_t_hdv=[]
pos_tref_hdv=[]
vel_tref_hdv=[]
acc_tref_hdv=[]

    for index in range(len(plot_data[0])):

        pos_t_hdv.append(test_results.test_run_comparision[time_step][index][1].detach().cpu().numpy())
        vel_t_hdv.append(test_results.test_run_comparision[time_step][index][3].detach().cpu().numpy())
        acc_t_hdv.append(test_results.test_run_comparision[time_step][index][5].detach().cpu().numpy())
        pos_tref_hdv.append(test_results.test_run_comparision[time_step][index][7].detach().cpu().numpy())
        vel_tref_hdv.append(test_results.test_run_comparision[time_step][index][9].detach().cpu().numpy())
        acc_tref_hdv.append(test_results.test_run_comparision[time_step][index][11].detach().cpu().numpy())

In [29]:
# Plotting outputs #
import matplotlib.colors as mcolors
####### For X - lateral#########
fig, ax = plt.subplots()
#plt.plot(y_ref,x_ref,'r',linewidth=2.0,label="Actual")
#plt.plot(y_pred,x_pred,'b',linewidth=2.0,label="Predicted")
plt.figure(facecolor='white')
plt.plot(pos_t_hdv,mcolors.CSS4_COLORS['salmon'],linewidth=2.0,label="Actual")
plt.plot(pos_tref_hdv,mcolors.CSS4_COLORS['limegreen'],linewidth=2.0,label="Predicted")
plt.xlabel('Time in (1/10)s')
plt.ylabel('Position along the road m')
plt.title('Comparision_of_position_along_road')
plt.legend()
plt.grid()
plt.savefig('graphs/irl_graphs/Comparision_rollout10_timestep_min20_posref_pospred_g1_p2_lr0005.png')
plt.close()

fig, ax = plt.subplots()
plt.figure(facecolor='white')
plt.plot(vel_t_hdv,mcolors.CSS4_COLORS['salmon'],linewidth=2.0,label="Actual")
plt.plot(vel_tref_hdv,mcolors.CSS4_COLORS['limegreen'],linewidth=2.0,label="Predicted")
plt.xlabel('Time in (1/10)s')
plt.ylabel('Velocity along the road in m/s')
plt.title('Comparision_Lateral_Velocities')
plt.legend()
plt.grid()
plt.savefig('graphs/irl_graphs/Comparision_rollout10_timestep_min20_vref_vpre_g1_p2_lr0005.png')
plt.close()

In [78]:
test_results.test_run_comparision[1][0]
#len(test_results.test_run_comparision)

[tensor(-46.4000, device='cuda:0'),
 tensor(-53.2063, device='cuda:0'),
 tensor(8., device='cuda:0'),
 tensor(7.4680, device='cuda:0'),
 tensor(-5., device='cuda:0'),
 tensor(-1.3502, device='cuda:0'),
 tensor(-31.8437, device='cuda:0', grad_fn=<UnbindBackward0>),
 tensor(-27.8377, device='cuda:0', grad_fn=<UnbindBackward0>),
 tensor(4.1773, device='cuda:0', grad_fn=<UnbindBackward0>),
 tensor(9.0293, device='cuda:0', grad_fn=<UnbindBackward0>),
 tensor(-1.2700, device='cuda:0', grad_fn=<UnbindBackward0>),
 tensor(0.0087, device='cuda:0', grad_fn=<UnbindBackward0>)]

In [202]:
'''
input = torch.randn(3, 5, requires_grad=True)
# each element in target has to have 0 <= value < C
target = torch.tensor([1, 0, 4])
output = torch.nn.functional.nll_loss(torch.nn.LogSoftmax(input, dim=1), target)
output.backward()
'''
m = nn.LogSoftmax(dim=1)
input = torch.randn(2, 3)
output = m(input)

input = torch.randn(3, 5, requires_grad=True)
target = torch.tensor([1, 0, 4])
output2 = torch.nn.functional.nll_loss(m(input), target)
